In [1]:
from nltk.stem import PorterStemmer
import string
import nltk
import json
import collections
import random
import numpy as np

In [2]:
# Stopword
stopword = []
with open('stopword', 'r') as f:
    for line in f:
        stopword.append(line.replace('\n', ''))

In [3]:
def my_parsing(word):
    # 0. Unicode
    word = str(word.decode('unicode_escape').encode('ascii','ignore').replace('\n', ''))
    if word == '':
        word = 'emoji'
    
    # 1. Remove punctuation
    word = word.translate(None, string.punctuation)
    if word == '':
        word = 'punctuation'
    
    # 2. To lower case
    word = word.lower()
    
    # 3. Remove Stopword
    word = ['' if x in stopword else x for x in word.split()]
    if word == '':
        word = ['stopword']
    
    # 4. Stem words
    word = [PorterStemmer().stem(x) for x in word]
    
    if word == []:
        word = ['notsure']

    return ' '.join(word)

In [4]:
pl_title = dict()
with open('title_list', 'r') as f:
    for line in f:
        pl_title[len(pl_title)] = my_parsing(line)

In [5]:
with open('processed_pl_title', 'w') as file:
     file.write(json.dumps(pl_title))

# Train Data

In [2]:
pl_title = json.load(open('processed_pl_title'))

In [3]:
pid_train = []
with open('../DATA_PROCESSING/PLAYLIST_INDEX_TRAIN_80.txt', 'r') as f:
    for line in f:
        pid_train.append(int(line.replace('\n', '')))

In [7]:
word_pl = dict()
for pid in pid_train:
    pid = str(pid)
    title = [x for x in pl_title[pid].split(' ') if x != '']
    for word in title:
        if word not in word_pl:
            word_pl[word] = [pid]
        else:
            word_pl[word].append(pid)

In [8]:
pl_track_train = json.load(open('../DATA_PROCESSING/PL_TRACKS_5_TRAIN.json'))

In [9]:
word_track = dict()
for word in word_pl:
    word_track[word] = []
    
for word in word_pl:
    for pid in word_pl[word]:
        word_track[word] += pl_track_train[str(pid)]

In [10]:
print 'hello'

hello


Tid to index

In [13]:
# all_track = []
# for pid in pl_track_train.keys():
#     for track in pl_track_train[pid]:
#         all_track.append(track)

# all_track = list(set(all_track))

# track_index = dict()
# for track in all_track:
#     track_index[track] = len(track_index)
    
# with open('TRACK_INDEX_READONLY.json', 'w') as file:
#      file.write(json.dumps(track_index))

track_index = json.load(open('TRACK_INDEX_READONLY.json'))

Title word to index

In [14]:
# word_index = dict()
# for each_word in word_track.keys():
#     word_index[each_word] = len(word_index)
    
# with open('WORD_INDEX_READONLY.json', 'w') as file:
#      file.write(json.dumps(word_index))

word_index = json.load(open('WORD_INDEX_READONLY.json'))

IDF

In [15]:
# num_docs = len(track_index)

# idf_word_index = {}
# for word in word_track:
#     # idf_i = lg (|D| / ( 1 + |{j: t_i in dj}||))
#     temp_idf = num_docs * 1.0 / (1 + len(list(set(word_track[word]))))
#     idf_word_index[word_index[word]] = temp_idf
    
# with open('WORD_IDF_WORD_INDEX_Nolog.json', 'w') as file:
#      file.write(json.dumps(idf_word_index))

idf_word_index = json.load(open('WORD_IDF_WORD_INDEX.json'))

Write [word -> track -> frequency] to file

In [23]:
with open('Word_Trackid_Frequency_Index_With_IDF', 'w') as f:
    for word in word_track.keys():
        #print word
        temp = dict(collections.Counter(word_track[word]))
        for tid in temp:
            f.write(str(word_index[word]) + ',' + str(track_index[tid]) + ',' + str(temp[tid] * 1.0 * idf_word_index[str(word_index[word])]) + '\n')

In [3]:
length = 0
with open('Word_Trackid_Frequency_Index_With_IDF', 'r') as f:
    for line in f:
        print line
        break

0,294858,2.91359209127



In [27]:
length

32108507

In [25]:
length

32108507

In [4]:
word_frequence_sum = {}
with open('Word_Trackid_Frequency_Index', 'r') as f:
    for line in f:
        temp = line.split(',')
        word_frequence_sum[temp[0]] = 0

In [5]:
len(word_frequence_sum)

9520

In [7]:
with open('Word_Trackid_Frequency_Index', 'r') as f:
    for line in f:
        temp = line.split(',')
        word_frequence_sum[temp[0]] += float(temp[2].replace('\n',''))

In [10]:
len(word_frequence_sum)

9520

In [19]:
with open('Word_Trackid_Frequency_Normalized', 'w') as f:
    with open('Word_Trackid_Frequency_Index', 'r') as f_old:
        for line in f_old:
            temp = line.split(',')
            print temp[0] + ',' + temp[1] + ',' + str(float(temp[2].replace('\n','')) / word_frequence_sum[temp[0]]) + '\n'
            #break
            #f.write(temp[0] + ',' + temp[1] + ',' + str(float(temp[2].replace('\n',''))/word_frequence_sum[temp[0]]) + '\n')

            

0,294858,0.00152207001522

0,506827,0.00152207001522

0,170767,0.00152207001522

0,28568,0.00152207001522

0,227845,0.00152207001522

0,279478,0.00152207001522

0,373108,0.00152207001522

0,323767,0.00152207001522

0,415277,0.00152207001522

0,37786,0.00152207001522

0,112809,0.00152207001522

0,446531,0.00152207001522

0,362708,0.00152207001522

0,85969,0.00152207001522

0,299012,0.00152207001522

0,245340,0.00152207001522

0,218570,0.00152207001522

0,203945,0.00152207001522

0,402015,0.00152207001522

0,41893,0.00152207001522

0,400974,0.00152207001522

0,385407,0.00152207001522

0,380319,0.00152207001522

0,399930,0.00152207001522

0,428780,0.00152207001522

0,388529,0.00152207001522

0,353510,0.00152207001522

0,326801,0.00152207001522

0,492278,0.00304414003044

0,359670,0.00152207001522

0,134535,0.00152207001522

0,202883,0.00152207001522

0,377246,0.00152207001522

0,502713,0.00152207001522

0,137686,0.00152207001522

0,414325,0.00152207001522

0,283688,0.00152207001522

0,398


2,283021,5.31208499336e-05

2,18833,0.000106241699867

2,431245,0.000159362549801

2,464565,5.31208499336e-05

2,393417,0.000318725099602

2,381730,5.31208499336e-05

2,245881,5.31208499336e-05

2,84366,5.31208499336e-05

2,51583,0.000424966799469

2,501337,0.000265604249668

2,398252,5.31208499336e-05

2,100806,5.31208499336e-05

2,51591,5.31208499336e-05

2,18848,5.31208499336e-05

2,183710,5.31208499336e-05

2,2429,5.31208499336e-05

2,117374,0.000106241699867

2,454223,5.31208499336e-05

2,266674,5.31208499336e-05

2,431272,5.31208499336e-05

2,51604,5.31208499336e-05

2,35150,5.31208499336e-05

2,84385,5.31208499336e-05

2,348785,0.000106241699867

2,511915,0.000265604249668

2,35158,5.31208499336e-05

2,299462,5.31208499336e-05

2,200243,5.31208499336e-05

2,283068,0.000106241699867

2,497914,5.31208499336e-05

2,448027,5.31208499336e-05

2,497919,5.31208499336e-05

2,266692,0.000212483399734

2,289187,5.31208499336e-05

2,183732,0.000212483399734

2,181100,0.000106241699867

2,

2,317831,5.31208499336e-05

2,119315,5.31208499336e-05

2,20730,5.31208499336e-05

2,367086,5.31208499336e-05

2,53473,5.31208499336e-05

2,274397,5.31208499336e-05

2,290549,5.31208499336e-05

2,516356,0.000371845949535

2,319649,0.000212483399734

2,59070,5.31208499336e-05

2,202145,5.31208499336e-05

2,433231,5.31208499336e-05

2,245773,5.31208499336e-05

2,383602,5.31208499336e-05

2,268606,0.000106241699867

2,285003,5.31208499336e-05

2,290612,5.31208499336e-05

2,499874,0.000159362549801

2,185567,5.31208499336e-05

2,69905,5.31208499336e-05

2,356403,0.000106241699867

2,135829,5.31208499336e-05

2,69912,5.31208499336e-05

2,251956,5.31208499336e-05

2,367109,5.31208499336e-05

2,277290,5.31208499336e-05

2,278501,5.31208499336e-05

2,350704,5.31208499336e-05

2,135834,5.31208499336e-05

2,334228,5.31208499336e-05

2,53500,5.31208499336e-05

2,367114,5.31208499336e-05

2,268630,5.31208499336e-05

2,290720,0.000106241699867

2,20759,5.31208499336e-05

2,152390,5.31208499336e-05



2,102952,5.31208499336e-05

2,336078,5.31208499336e-05

2,38849,5.31208499336e-05

2,204301,5.31208499336e-05

2,137687,5.31208499336e-05

2,1003,5.31208499336e-05

2,88083,5.31208499336e-05

2,352529,0.000106241699867

2,402079,5.31208499336e-05

2,170852,5.31208499336e-05

2,451799,5.31208499336e-05

2,352531,5.31208499336e-05

2,303223,5.31208499336e-05

2,466893,5.31208499336e-05

2,485049,5.31208499336e-05

2,104574,5.31208499336e-05

2,82947,5.31208499336e-05

2,65950,5.31208499336e-05

2,526596,5.31208499336e-05

2,157292,5.31208499336e-05

2,204029,5.31208499336e-05

2,352541,5.31208499336e-05

2,485060,5.31208499336e-05

2,170872,0.000159362549801

2,433690,5.31208499336e-05

2,55335,5.31208499336e-05

2,433715,5.31208499336e-05

2,369045,5.31208499336e-05

2,169403,5.31208499336e-05

2,336106,5.31208499336e-05

2,270510,5.31208499336e-05

2,77442,0.000159362549801

2,319733,0.000106241699867

2,146245,5.31208499336e-05

2,187443,5.31208499336e-05

2,518310,5.31208499336e-05


2,40579,5.31208499336e-05

2,47682,5.31208499336e-05

2,370741,5.31208499336e-05

2,89879,5.31208499336e-05

2,106316,5.31208499336e-05

2,122942,5.31208499336e-05

2,288523,5.31208499336e-05

2,304968,5.31208499336e-05

2,155997,5.31208499336e-05

2,326881,0.000106241699867

2,503487,0.000106241699867

2,387228,5.31208499336e-05

2,468498,0.000106241699867

2,122951,5.31208499336e-05

2,370760,5.31208499336e-05

2,40597,0.000106241699867

2,52030,5.31208499336e-05

2,172618,5.31208499336e-05

2,30749,0.000106241699867

2,272161,5.31208499336e-05

2,524387,5.31208499336e-05

2,222385,0.000106241699867

2,312304,0.000371845949535

2,470157,0.000265604249668

2,354312,5.31208499336e-05

2,24299,5.31208499336e-05

2,520065,0.000106241699867

2,436968,5.31208499336e-05

2,7953,5.31208499336e-05

2,520073,0.000371845949535

2,40624,0.000106241699867

2,7957,5.31208499336e-05

2,420305,0.000212483399734

2,453618,5.31208499336e-05

2,337881,5.31208499336e-05

2,189213,5.31208499336e-05

2,58

...

50,424119,1.73035827068e-05

50,424121,8.6517913534e-06

50,512779,1.73035827068e-05

50,169890,1.73035827068e-05

50,159920,1.73035827068e-05

50,424125,8.6517913534e-06

50,292365,1.73035827068e-05

50,424127,8.6517913534e-06

50,93704,8.6517913534e-06

50,490717,8.6517913534e-06

50,490722,8.6517913534e-06

50,358136,8.6517913534e-06

50,445288,8.6517913534e-06

50,93711,8.6517913534e-06

50,226333,8.6517913534e-06

50,28093,8.6517913534e-06

50,522233,2.59553740602e-05

50,226337,8.6517913534e-06

50,226339,8.6517913534e-06

50,292386,1.73035827068e-05

50,367395,8.6517913534e-06

50,292388,1.73035827068e-05

50,159947,8.6517913534e-06

50,26453,8.6517913534e-06

50,93729,2.59553740602e-05

50,93730,8.6517913534e-06

50,28112,8.6517913534e-06

50,358157,3.46071654136e-05

50,205297,8.6517913534e-06

50,424159,8.6517913534e-06

50,226356,8.6517913534e-06

50,28117,8.6517913534e-06

50,455837,8.6517913534e-06

50,358169,1.73035827068e-05

50,424168,5.19107481204e-05

50,296728,8.6517


50,96892,8.6517913534e-06

50,57309,8.6517913534e-06

50,163181,8.6517913534e-06

50,229572,0.000337419862783

50,158775,8.6517913534e-06

50,31343,8.6517913534e-06

50,229576,8.6517913534e-06

50,295558,4.3258956767e-05

50,467404,1.73035827068e-05

50,427334,1.73035827068e-05

50,427337,1.73035827068e-05

50,229580,8.6517913534e-06

50,361323,6.92143308272e-05

50,493984,8.6517913534e-06

50,361326,8.6517913534e-06

50,423011,8.6517913534e-06

50,214053,8.6517913534e-06

50,31363,8.6517913534e-06

50,229593,8.6517913534e-06

50,163204,8.6517913534e-06

50,229594,0.000242250157895

50,163206,1.73035827068e-05

50,229595,8.6517913534e-05

50,81658,8.6517913534e-06

50,31369,8.6517913534e-06

50,96926,8.6517913534e-06

50,361351,1.73035827068e-05

50,31373,8.6517913534e-06

50,401072,8.6517913534e-06

50,147684,8.6517913534e-06

50,163227,8.6517913534e-06

50,361357,8.6517913534e-06

50,427380,8.6517913534e-06

50,5192,8.6517913534e-06

50,57594,2.59553740602e-05

50,361361,8.651791353

50,298892,2.59553740602e-05

50,100265,8.6517913534e-06

50,473937,8.6517913534e-06

50,364666,8.6517913534e-06

50,192467,8.6517913534e-06

50,77243,8.6517913534e-06

50,364481,8.6517913534e-06

50,497365,1.73035827068e-05

50,166488,8.6517913534e-06

50,497367,8.6517913534e-06

50,364675,8.6517913534e-06

50,232907,8.6517913534e-06

50,298906,8.6517913534e-06

50,341691,8.6517913534e-06

50,298911,8.6517913534e-06

50,364681,3.46071654136e-05

50,232915,8.6517913534e-06

50,34665,8.6517913534e-06

50,166507,8.6517913534e-06

50,298919,6.05625394738e-05

50,430745,8.6517913534e-06

50,364688,8.6517913534e-06

50,77384,8.6517913534e-06

50,430753,5.19107481204e-05

50,166516,8.6517913534e-06

50,34680,8.6517913534e-06

50,34681,8.6517913534e-06

50,298935,8.6517913534e-06

50,298936,8.6517913534e-06

50,497392,8.6517913534e-06

50,100312,8.6517913534e-06

50,209806,8.6517913534e-06

50,148268,8.6517913534e-06

50,34689,8.6517913534e-06

50,270030,8.6517913534e-06

50,303070,8.651791353


50,367319,8.6517913534e-06

50,301543,8.6517913534e-06

50,235531,8.6517913534e-06

50,367324,1.73035827068e-05

50,367325,8.6517913534e-06

50,60815,8.6517913534e-06

50,37290,8.6517913534e-06

50,17097,1.73035827068e-05

50,500088,1.73035827068e-05

50,433474,8.6517913534e-06

50,37292,8.6517913534e-06

50,367329,8.6517913534e-06

50,37296,8.6517913534e-06

50,93288,8.6517913534e-06

50,38843,8.6517913534e-06

50,367337,8.6517913534e-06

50,169192,1.73035827068e-05

50,367340,1.73035827068e-05

50,102935,8.6517913534e-06

50,433490,2.59553740602e-05

50,102938,8.6517913534e-06

50,357796,0.00038067881955

50,37311,8.6517913534e-06

50,27966,1.73035827068e-05

50,102943,8.6517913534e-06

50,259384,8.6517913534e-06

50,433498,8.6517913534e-06

50,301579,8.6517913534e-06

50,490426,8.6517913534e-06

50,93409,8.6517913534e-06

50,170846,8.6517913534e-06

50,261572,1.73035827068e-05

50,358006,1.73035827068e-05

50,500117,8.6517913534e-06

50,102955,2.59553740602e-05

50,38853,3.46071654

KeyboardInterrupt: 

In [21]:
with open('Word_Trackid_Frequency_Normalized_Alpha', 'w') as f:
    with open('Word_Trackid_Frequency_Index', 'r') as f_old:
        for line in f_old:
            temp = line.split(',')
            #print temp[0] + ',' + temp[1] + ',' + str(float(temp[2].replace('\n','')) * 50.0 / word_frequence_sum[temp[0]]) + '\n'
            #break
            f.write(temp[0] + ',' + temp[1] + ',' + str(float(temp[2].replace('\n','')) * 50.0 / word_frequence_sum[temp[0]]) + '\n')

           